In [284]:
import numpy as np
import random
import math
import matplotlib.pyplot as plt

### 定義目標函數

In [285]:
def fitness(x1, x2):
    u = (1+(x1+x2+1)**2*(19-14*x1+3*x1**2-14*x2+6*x1*x2+3*x2**2))
    v = (30+(2*x1-3*x2)**2*(18-32*x1+12*x1**2+48*x2-36*x1*x2+27*x2**2))
    return u*v

### 定義 Simplex Direct Search

In [286]:
n = 2
def simplex(init_sol, n = n, edge_length = 2):
    sx_sol = []
    if init_sol[0] + edge_length > 2:
        sx_sol.append([round(init_sol[0] - edge_length, 4), init_sol[1]])
    else:
        sx_sol.append([round(init_sol[0] + edge_length, 4), init_sol[1]])
    if init_sol[1] + edge_length > 2:
        sx_sol.append([init_sol[0], round(init_sol[1] - edge_length, 4)])
    else:
        sx_sol.append([init_sol[0], round(init_sol[1] + edge_length, 4)])
    return sx_sol

### 計算重心

In [323]:
def centroid(dataset):
    x1_sum = 0; x2_sum = 0
    for i in range(len(dataset)):
        x1_sum += dataset[i][0] 
        x2_sum += dataset[i][1]
    return round(x1_sum/(len(dataset)), 4), round(x2_sum/(len(dataset)), 4)

### 參數設定

In [342]:
# step0 Setting parameters
np.random.seed(11)
# 變數數量、每個溫度迭代次數

n = 2
M = 10*n
MaxIter = 1000*n

# sigma & accepted probability & termination criteria
sigma = np.random.rand()
p = 0.9                    #initial
epsilon = 1e-6 

# 溫度衰減係數
alpha = 0.9

# 初始解
curx = [round(random.uniform(-2, 2), 4), round(random.uniform(-2, 2), 4)]
print("初始解：", curx)

# Simplex Direct Search
S = []; SortedS=[]
S.append(curx)
S.extend(simplex(curx))
print("Original solution set: %s" %S)
fit_list = []
for i1 in range(len(S)):
    x1 = S[i1][0]; x2 = S[i1][1]
    fit_list.append([i1, fitness(x1, x2)])

初始解： [-0.4056, -0.9563]
Original solution set: [[-0.4056, -0.9563], [1.5944, -0.9563], [-0.4056, 1.0437]]


In [340]:
import time
tStart = time.time() #計時開始

# step1: Order & re-label
for j1 in range(len(S)):
    SortedS.append(S[sorted(fit_list,key = lambda fit_list: fit_list[1])[j1][0]])
print(len(SortedS))
curx = SortedS[0]
minfit = sorted(fit_list,key = lambda fit_list: fit_list[1])[0][1]
maxfit = sorted(fit_list,key = lambda fit_list: fit_list[1])[-1][1]

# 初始溫度、溫度下限
maxT = (maxfit-minfit)/np.exp(p) # initial p = 0.9
curT = maxT
minT = 1e-5 * maxT
print('初始溫度: %.f & 終止溫度: %.f' %(curT, minT))

print('初始解(x1): %s & 初始目標函數值(f[x1]): %.f' %(curx, minfit))

#print(SortedS)
# step2
iters = 1
while (maxfit-minfit) >= epsilon and curT > minT and iters <= MaxIter:
    # step3
    for epoch in range(M):
        #step3.1
        k = 1
        print(SortedS)
        #step3.2
        while k <= n:
            shrink = True
            #step3.3 Reflect
            #print(SortedS[:n-k+1])
            center = centroid(SortedS[:n-k+1])
            #print('重心:', center)
            x1 = SortedS[-k][0]; x2 = SortedS[-k][1]
            ρ_ = random.uniform(0.9, 1.1) 
            #print(ρ_)
            if round(center[0] + ρ_*(center[0] - x1),4) > 2 or round(center[0] + ρ_*(center[0] - x1),4) < -2:
                x1_r = round(center[0] - ρ_*(center[0] - x1),4)
            else:
                x1_r = round(center[0] + ρ_*(center[0] - x1),4)
            if round(center[1] + ρ_*(center[1] - x2),4) > 2 or round(center[1] + ρ_*(center[1] - x2),4) < -2:
                x2_r = round(center[1] - ρ_*(center[1] - x2),4)
            else:
                x2_r = round(center[1] + ρ_*(center[1] - x2),4)  
                
            #print('Before Reflect :', x1, x2)
            #print('Reflected :', x1_r, x2_r)
            f_min = fitness(x1_r, x2_r)
            #print('New fitness %.f'%f_min)
            #step3.3.1
            if f_min < minfit:
                #step3.3.3
                SortedS[-k] = [x1_r, x2_r]
                #minfit = f_min
                # step3.5
                fit_list_1 = []
                for i2 in range(len(SortedS)):
                    x1 = SortedS[i2][0]; x2 = SortedS[i2][1]
                    fit_list_1.append([i2, fitness(x1, x2)])
                S_ = []    
                for j2 in range(len(SortedS)):
                    S_.append(SortedS[sorted(fit_list_1,key = lambda fit_list_1: fit_list_1[1])[j2][0]])
                curx = S_[0]
                SortedS = S_
                minfit = sorted(fit_list_1,key = lambda fit_list_1: fit_list_1[1])[0][1]
                maxfit = sorted(fit_list_1,key = lambda fit_list_1:fit_list_1[1])[-1][1]
                print('當下最佳解: %s & fitness: %.f' %(curx, minfit))
                shrink = False
                epoch += 1
                break
            #step3.3.2
            else:
                p = np.exp(-(f_min-minfit)/curT)
                #print('Prob: %.2f' %p)
                if p >= np.random.rand():
                    SortedS[-k] = [x1_r, x2_r]
                    fit_list_2 = []
                    for i3 in range(len(SortedS)):
                        x1 = SortedS[i3][0]; x2 = SortedS[i3][1]
                        fit_list_2.append([i3, fitness(x1, x2)])
                    #print(SortedS)
                    S_ = []    
                    for j3 in range(len(SortedS)):
                        S_.append(SortedS[sorted(fit_list_2,key = lambda fit_list_2: fit_list_2[1])[j3][0]])
                    curx = S_[0]
                    SortedS = S_
                    minfit = sorted(fit_list_2,key = lambda fit_list: fit_list_2[1])[0][1]
                    maxfit = sorted(fit_list_2,key = lambda fit_list: fit_list_2[1])[-1][1]
                    print('當下最佳解: %s & fitness: %.f' %(curx, minfit))
                    shrink = False
                    epoch += 1
                    break
                else:
                    print('K %s' %k)
                    k += 1
                    
                    
                    
        #else:
        # shrink
        if shrink:            
            #print('Before shrink %s' % SortedS)
            S = [SortedS[0]]
            for val in range(1,3):
                x1 = SortedS[-val][0]; x2 = SortedS[-val][1]
                x1_s = round(SortedS[0][0] + sigma*(x1 - SortedS[0][0]), 4)
                x2_s = round(SortedS[0][1] + sigma*(x2 - SortedS[0][1]), 4)
                S.append([x1_s, x2_s])

            #print('After shrink %s' % S)

                # 計算 排序
            fit_list_3 = []
            for i4 in range(len(S)):
                x1 = S[i4][0]; x2 = S[i4][1]
                fit_list_3.append([i4, fitness(x1, x2)])
            SortedS = []    
            for j4 in range(len(S)):
                SortedS.append(S[sorted(fit_list_3,key = lambda fit_list_3: fit_list_3[1])[j4][0]])
            curx = SortedS[0]
            minfit = sorted(fit_list,key = lambda fit_list: fit_list[1])[0][1]
            maxfit = sorted(fit_list,key = lambda fit_list: fit_list[1])[-1][1]
            print('當下最佳解: %s & fitness: %.f' %(curx, minfit))
            

        print('-'*10, 'end of epoch %s' %epoch, '-'*10)                            
        epoch += 1        
    curT *= alpha    
    iters += 1
    print('-'*10,'current temperature %.f & iterations %.f & fitness = %.f' %(curT, iters, minfit), '-'*10)
print('最終收斂的解與解的品質:' , curx, minfit)
tEnd = time.time()#計時結束
print ("It cost %f sec" % (tEnd - tStart))

3
初始溫度: 26983 & 終止溫度: 0
初始解(x1): [0.6743, -1.0334] & 初始目標函數值(f[x1]): 1683
[[0.6743, -1.0334], [0.6743, 0.9666], [-1.3257, 0.9666]]
當下最佳解: [0.6743, -1.0334] & fitness: 1683
---------- end of epoch 1 ----------
[[0.6743, -1.0334], [0.6743, 0.9666], [-1.4537, -1.0974]]
K 1
當下最佳解: [0.6743, -1.0334] & fitness: 1683
---------- end of epoch 2 ----------
[[0.6743, -1.0334], [-1.4537, -1.0974], [0.6743, 1.146]]
K 1
當下最佳解: [0.6743, -1.0334] & fitness: 1683
---------- end of epoch 3 ----------
[[0.6743, -1.0334], [-1.3654, -0.9721], [0.6743, 1.146]]
當下最佳解: [0.6743, -1.0334] & fitness: 1683
---------- end of epoch 4 ----------
[[0.6743, -1.0334], [-1.3654, -0.9721], [-1.286, 0.9788]]
當下最佳解: [0.6743, -1.0334] & fitness: 1683
---------- end of epoch 5 ----------
[[0.6743, -1.0334], [-1.3654, -0.9721], [0.625, 1.042]]
K 1
當下最佳解: [0.6743, -1.0334] & fitness: 1683
---------- end of epoch 6 ----------
[[0.6743, -1.0334], [-1.2682, -1.0918], [0.625, 1.042]]
K 1
當下最佳解: [0.6743, -1.0334] & fitness: 1683
--

---------- end of epoch 11 ----------
[[0.0818, -0.9956], [-0.047, -0.945], [-0.1386, -1.0655]]
當下最佳解: [0.0818, -0.9956] & fitness: 5
---------- end of epoch 12 ----------
[[0.0818, -0.9956], [-0.047, -0.945], [0.1689, -0.8779]]
當下最佳解: [0.0818, -0.9956] & fitness: 5
---------- end of epoch 13 ----------
[[0.0818, -0.9956], [-0.047, -0.945], [-0.1482, -1.0713]]
當下最佳解: [0.0818, -0.9956] & fitness: 5
---------- end of epoch 14 ----------
[[0.0818, -0.9956], [-0.047, -0.945], [0.1767, -0.8731]]
當下最佳解: [0.0818, -0.9956] & fitness: 5
---------- end of epoch 15 ----------
[[0.0818, -0.9956], [-0.047, -0.945], [-0.1451, -1.0694]]
當下最佳解: [0.0818, -0.9956] & fitness: 5
---------- end of epoch 16 ----------
[[0.0818, -0.9956], [-0.047, -0.945], [0.1679, -0.8785]]
當下最佳解: [0.0818, -0.9956] & fitness: 5
---------- end of epoch 17 ----------
[[0.0818, -0.9956], [-0.047, -0.945], [-0.1194, -1.0538]]
當下最佳解: [0.0818, -0.9956] & fitness: 5
---------- end of epoch 18 ----------
[[0.0818, -0.9956], [-0.047

[[0.0508, -0.9946], [-0.1435, -1.064], [-0.2227, -1.0401]]
當下最佳解: [0.0508, -0.9946] & fitness: 4
---------- end of epoch 2 ----------
[[0.0508, -0.9946], [-0.1435, -1.064], [0.1261, -1.0187]]
當下最佳解: [0.0508, -0.9946] & fitness: 4
---------- end of epoch 3 ----------
[[0.0508, -0.9946], [-0.1435, -1.064], [-0.2259, -1.0403]]
當下最佳解: [0.0508, -0.9946] & fitness: 4
---------- end of epoch 4 ----------
[[0.0508, -0.9946], [-0.1435, -1.064], [0.1293, -1.0185]]
當下最佳解: [0.0508, -0.9946] & fitness: 4
---------- end of epoch 5 ----------
[[0.0508, -0.9946], [-0.1435, -1.064], [-0.2114, -1.0395]]
當下最佳解: [0.0508, -0.9946] & fitness: 4
---------- end of epoch 6 ----------
[[0.0508, -0.9946], [-0.1435, -1.064], [0.1201, -1.019]]
當下最佳解: [0.0508, -0.9946] & fitness: 4
---------- end of epoch 7 ----------
[[0.0508, -0.9946], [-0.1435, -1.064], [-0.1988, -1.0387]]
當下最佳解: [0.0508, -0.9946] & fitness: 4
---------- end of epoch 8 ----------
[[0.0508, -0.9946], [0.0923, -1.0208], [-0.1435, -1.064]]
當下最佳解: [

---------- end of epoch 9 ----------
[[0.0348, -0.9958], [0.0996, -0.9163], [0.0289, -0.9014]]
當下最佳解: [0.0348, -0.9958] & fitness: 3
---------- end of epoch 10 ----------
[[0.0348, -0.9958], [0.0996, -0.9163], [0.1058, -1.0112]]
當下最佳解: [0.0348, -0.9958] & fitness: 3
---------- end of epoch 11 ----------
[[0.0348, -0.9958], [0.0996, -0.9163], [0.0265, -0.898]]
當下最佳解: [0.0348, -0.9958] & fitness: 3
---------- end of epoch 12 ----------
[[0.0348, -0.9958], [0.0996, -0.9163], [0.1089, -1.0157]]
當下最佳解: [0.0348, -0.9958] & fitness: 3
---------- end of epoch 13 ----------
[[0.0348, -0.9958], [0.0996, -0.9163], [0.0215, -0.8908]]
當下最佳解: [0.0348, -0.9958] & fitness: 3
---------- end of epoch 14 ----------
[[0.0348, -0.9958], [0.0996, -0.9163], [0.1095, -1.0165]]
當下最佳解: [0.0348, -0.9958] & fitness: 3
---------- end of epoch 15 ----------
[[0.0348, -0.9958], [0.0996, -0.9163], [0.0268, -0.8984]]
當下最佳解: [0.0348, -0.9958] & fitness: 3
---------- end of epoch 16 ----------
[[0.0348, -0.9958], [0.099

---------- end of epoch 12 ----------
[[-0.0063, -1.0068], [0.0055, -0.9905], [-0.0279, -1.0055]]
當下最佳解: [-0.0063, -1.0068] & fitness: 3
---------- end of epoch 13 ----------
[[-0.0063, -1.0068], [0.0055, -0.9905], [0.0247, -0.9925]]
當下最佳解: [-0.0063, -1.0068] & fitness: 3
---------- end of epoch 14 ----------
[[-0.0063, -1.0068], [0.0055, -0.9905], [-0.0247, -1.0047]]
當下最佳解: [-0.0063, -1.0068] & fitness: 3
---------- end of epoch 15 ----------
[[-0.0063, -1.0068], [0.0055, -0.9905], [0.0223, -0.9931]]
當下最佳解: [-0.0063, -1.0068] & fitness: 3
---------- end of epoch 16 ----------
[[-0.0063, -1.0068], [0.0055, -0.9905], [-0.0223, -1.0041]]
當下最佳解: [-0.0063, -1.0068] & fitness: 3
---------- end of epoch 17 ----------
[[-0.0063, -1.0068], [0.0055, -0.9905], [0.0201, -0.9936]]
當下最佳解: [-0.0063, -1.0068] & fitness: 3
---------- end of epoch 18 ----------
[[-0.0063, -1.0068], [0.0055, -0.9905], [-0.0222, -1.0041]]
當下最佳解: [-0.0063, -1.0068] & fitness: 3
---------- end of epoch 19 ----------
[[-0.0

...

當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 17 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 18 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 19 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 20 ----------
---------- current temperature 0 & iterations 1929 & fitness = 3 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 1 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 2 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 3 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, 

K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 2 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 3 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 4 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 5 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 6 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 7 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 8 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 9 ----------
[[-0.0001, -1.0], [-

當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 7 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 8 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 9 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 10 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 11 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 12 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 13 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 14 ----------
[[-0.0001, -1.0], [

---------- end of epoch 12 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 13 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 14 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 15 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 16 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 17 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 18 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 19 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]


---------- end of epoch 17 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 18 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 19 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 20 ----------
---------- current temperature 0 & iterations 1994 & fitness = 3 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 1 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 2 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of epoch 3 ----------
[[-0.0001, -1.0], [-0.0001, -1.0], [-0.0, -0.9999]]
K 1
當下最佳解: [-0.0001, -1.0] & fitness: 3
---------- end of

In [332]:
print('最終收斂的解與解的品質:' , curx, minfit)

最終收斂的解與解的品質: [-0.0, -1.0] 3.0
